## DSpy Prompt Optimisation for Multi-Hop (CoT) QA (Baleen Architecture) with Assertions

A single search query is often not enough for complex QA tasks. For instance, an example within HotPotQA includes a question about the birth city of the writer of "Right Back At It Again". A search query often identifies the author correctly as "Jeremy McKinnon", but lacks the capability to compose the intended answer in determining when he was born.

The standard approach for this challenge in retrieval-augmented NLP literature is to build multi-hop search systems, like GoldEn (Qi et al., 2019) and Baleen (Khattab et al., 2021). These systems read the retrieved results and then generate additional queries to gather additional information when necessary before arriving to a final answer. Using DSPy, we can simulate such systems in a few lines of code.

Refer to https://arxiv.org/pdf/2101.00436.pdf for a explanation of the Baleen architecture.


In [4]:
%env pip install -qU langchain-ibm

env: pip=install -qU langchain-ibm


In [5]:
import dspy
from dsp.utils import deduplicate
from dspy.datasets import HotPotQA
from dspy.predict.retry import Retry
from dspy.teleprompt import BootstrapFewShot, BootstrapFewShotWithRandomSearch
from dspy.evaluate.evaluate import Evaluate
from dspy.primitives.assertions import assert_transform_module, backtrack_handler

import os
import requests
from dsp import LM
import dspy

In [8]:
os.environ['WATSONX_URL']="https://us-south.ml.cloud.ibm.com/ml/v1/text/generation?version=2023-05-29"
os.environ['WATSONX_APIKEY']=""
os.environ['WATSONX_PROJECTID']=""

### Create Implementation of DSpy LM Class for watsonx.ai models

In [9]:
class Watson(LM):
    def __init__(self,model,api_key):
        self.kwargs = {
            "model": model,
            "temperature": 0.0,
            "max_tokens": 150,
            "top_p": 1,
            "frequency_penalty": 0,
            "presence_penalty": 0,
            "n": 1,
        }
        self.model = model
        self.api_key = api_key
        self.provider = "default"
        self.history = []
        
        self.base_url = os.environ['WATSONX_URL']

        self.project_id = os.environ['WATSONX_PROJECTID']

    def basic_request(self, prompt: str, **kwargs):
        headers = {
            "Authorization": f"Bearer {self.api_key}",
            "Accept": "application/json",
            "content-type": "application/json"
        }

        data = {
            "parameters": {**kwargs},
            "model_id": self.model,
            "input": prompt,
            "project_id": self.project_id
        }

        response = requests.post(self.base_url, headers=headers, json=data)
        response = response.json()

        self.history.append({
            "prompt": prompt,
            "response": response,
            "kwargs": kwargs,
        })
        return response

    def __call__(self, prompt, only_completed=True, return_sorted=False, **kwargs):
        response = self.request(prompt, **kwargs)

        print(response)

        completions = [result["generated_text"] for result in response["results"]]

        return completions

### Configure DSpy with the watsonx.ai Language Model

In [10]:
import requests

def generate_access_token(api_key):
    headers={}
    headers["Content-Type"] = "application/x-www-form-urlencoded"
    headers["Accept"] = "application/json"
    data = {
        "grant_type": "urn:ibm:params:oauth:grant-type:apikey",
        "apikey": api_key
    }
    response = requests.post('https://iam.cloud.ibm.com/identity/token', data=data, headers=headers)
    json_data = response.json()
    iam_access_token = json_data['access_token']
    return iam_access_token

token = generate_access_token(os.environ['WATSONX_APIKEY'])

In [11]:
watsonx = Watson(model="meta-llama/llama-2-70b-chat",api_key=token)
dspy.settings.configure(lm=watsonx, trace=[], temperature=0.7)

### Collect the data

In [12]:
colbertv2_wiki17_abstracts = dspy.ColBERTv2(url='http://20.102.90.50:2017/wiki17_abstracts')
dspy.settings.configure(rm=colbertv2_wiki17_abstracts)

dataset = HotPotQA(train_seed=1, train_size=300, eval_seed=2023, dev_size=300, test_size=0)
trainset = [x.with_inputs('question') for x in dataset.train]
devset = [x.with_inputs('question') for x in dataset.dev]

### Helper Functions & Optimiser Metrics

In [13]:
# Suggestion helper functions and Teleprompter metric

def validate_query_distinction_local(previous_queries, query):
    """check if query is distinct from previous queries"""
    if previous_queries == []:
        return True
    if dspy.evaluate.answer_exact_match_str(query, previous_queries, frac=0.8):
        return False
    return True

def validate_context_and_answer_and_hops(example, pred, trace=None):
    if not dspy.evaluate.answer_exact_match(example, pred):
        return False

    if not dspy.evaluate.answer_passage_match(example, pred):
        return False

    return True


In [14]:
# Extrinsic metrics

def gold_passages_retrieved(example, pred, trace=None):
    gold_titles = set(map(dspy.evaluate.normalize_text, example['gold_titles']))

    print(gold_titles)

    found_titles = set(map(dspy.evaluate.normalize_text, [c.split(' | ')[0] for c in pred.context]))

    print(found_titles)

    return gold_titles.issubset(found_titles)

### Signature of the DSpy Modules

In [15]:
class GenerateAnswer(dspy.Signature):
    """Answer questions with short factoid answers."""

    context = dspy.InputField(desc="may contain relevant facts")
    question = dspy.InputField()
    answer = dspy.OutputField(desc="often between 1 and 5 words")


class GenerateSearchQuery(dspy.Signature):
    """Write a simple search query that will help answer a complex question."""

    context = dspy.InputField(desc="may contain relevant facts")
    question = dspy.InputField()
    query = dspy.OutputField()

In [16]:
# returns distinct queries from previous queries
def all_queries_distinct(prev_queries):
    query_distinct = True
    for i, query in enumerate(prev_queries):
        if validate_query_distinction_local(prev_queries[:i], query) == False:
            query_distinct = False
            break
    return query_distinct

### DSpy Modules

In [17]:
class SimplifiedBaleen(dspy.Module):
    def __init__(self, passages_per_hop=2, max_hops=2):
        super().__init__()

        self.generate_query = [dspy.ChainOfThought(GenerateSearchQuery) for _ in range(max_hops)]
        self.retrieve = dspy.Retrieve(k=passages_per_hop)
        self.generate_answer = dspy.ChainOfThought(GenerateAnswer)
        self.max_hops = max_hops

        # for evaluating assertions only
        self.passed_suggestions = 0

    def forward(self, question):
        context = []
        prev_queries = [question]

        for hop in range(self.max_hops):
            query = self.generate_query[hop](context=context, question=question).query
            prev_queries.append(query)
            passages = self.retrieve(query).passages
            context = deduplicate(context + passages)
        
        if all_queries_distinct(prev_queries):
            self.passed_suggestions += 1
        
        pred = self.generate_answer(context=context, question=question)
        pred = dspy.Prediction(context=context, answer=pred.answer)
        return pred

In [18]:
class SimplifiedBaleenAssertions(dspy.Module):
    def __init__(self, passages_per_hop=2, max_hops=2):
        super().__init__()
        self.generate_query = [dspy.ChainOfThought(GenerateSearchQuery) for _ in range(max_hops)]
        self.retrieve = dspy.Retrieve(k=passages_per_hop)
        self.generate_answer = dspy.ChainOfThought(GenerateAnswer)
        self.max_hops = max_hops

        # for evaluating assertions only
        self.passed_suggestions = 0

    def forward(self, question):
        context = []
        prev_queries = [question]

        for hop in range(self.max_hops):
            query = self.generate_query[hop](context=context, question=question).query

            dspy.Suggest(
                len(query) <= 100,
                "Query should be short and less than 100 characters",
            )

            dspy.Suggest(
                validate_query_distinction_local(prev_queries, query),
                "Query should be distinct from: "
                + "; ".join(f"{i+1}) {q}" for i, q in enumerate(prev_queries)),
            )

            prev_queries.append(query)
            passages = self.retrieve(query).passages
            context = deduplicate(context + passages)
        
        if all_queries_distinct(prev_queries):
            self.passed_suggestions += 1

        pred = self.generate_answer(context=context, question=question)
        pred = dspy.Prediction(context=context, answer=pred.answer)
        return pred


In [19]:
evaluate_on_hotpotqa = Evaluate(devset=devset, num_threads=10, display_progress=True, display_table=False)

In [20]:
def evaluate(module):
    module.passed_suggestions = 0

    retrieval_score = evaluate_on_hotpotqa(
        module, metric=gold_passages_retrieved
    )
    
    suggestions_score = module.passed_suggestions / len(devset) * 100

    accuracy_score = evaluate_on_hotpotqa(
        module, metric=dspy.evaluate.answer_exact_match
    )

    print(f"## Suggestions Score: {suggestions_score}")
    print(f"## Retrieval Score: {retrieval_score}")
    print(f"## Accuracy Score: {accuracy_score}")

In [16]:
# No Compilation + No Assertion
baleen = SimplifiedBaleen()
evaluate(baleen)

  0%|          | 0/300 [00:00<?, ?it/s]

{'model_id': 'ibm/granite-13b-instruct-v2', 'created_at': '2024-04-08T12:41:40.755Z', 'results': [{'generated_text': ' ${produce the query}. Cangzhou and Qionghai are cities in Hebei', 'generated_token_count': 20, 'input_token_count': 114, 'stop_reason': 'max_tokens'}]}
{'model_id': 'ibm/granite-13b-instruct-v2', 'created_at': '2024-04-08T12:41:40.756Z', 'results': [{'generated_text': ' ${produce the query}. Gene was a 90s rock band that reformed in 2004. The', 'generated_token_count': 20, 'input_token_count': 113, 'stop_reason': 'max_tokens'}]}
{'model_id': 'ibm/granite-13b-instruct-v2', 'created_at': '2024-04-08T12:41:40.753Z', 'results': [{'generated_text': ' ${produce the query}. The Crichton Collegiate Church is located near the River South E', 'generated_token_count': 20, 'input_token_count': 107, 'stop_reason': 'max_tokens'}]}
{'model_id': 'ibm/granite-13b-instruct-v2', 'created_at': '2024-04-08T12:41:40.796Z', 'results': [{'generated_text': ' ${produce the query}. The action of

Average Metric: 1 / 1  (100.0):   0%|          | 1/300 [00:06<29:59,  6.02s/it]

{'model_id': 'ibm/granite-13b-instruct-v2', 'created_at': '2024-04-08T12:41:45.459Z', 'results': [{'generated_text': 'River Tyne is a river in Midlothian, Scotland.', 'generated_token_count': 16, 'input_token_count': 437, 'stop_reason': 'eos_token'}]}
{'crichton collegiate church', 'crichton castle'}
{'crichton collegiate church', 'haltwhistle a69 bridge west', 'crichton castle', 'haltwhistle a69 bridge east'}
{'model_id': 'ibm/granite-13b-instruct-v2', 'created_at': '2024-04-08T12:41:45.551Z', 'results': [{'generated_text': ' ${produce the answer}. The Afghan Whigs reformed in 2008. Gene was a band active', 'generated_token_count': 20, 'input_token_count': 593, 'stop_reason': 'max_tokens'}]}
{'model_id': 'ibm/granite-13b-instruct-v2', 'created_at': '2024-04-08T12:41:45.643Z', 'results': [{'generated_text': ' answer this question. The NHL Entry Draft is conducted by the NHL. Marc-Andre Fleury', 'generated_token_count': 20, 'input_token_count': 477, 'stop_reason': 'max_tokens'}]}
{'mode

Average Metric: 1 / 4  (25.0):   1%|          | 3/300 [00:06<14:29,  2.93s/it] 

...

{'model_id': 'ibm/granite-13b-instruct-v2', 'created_at': '2024-04-08T12:47:23.339Z', 'results': [{'generated_text': 'Sachin Khedekar', 'generated_token_count': 8, 'input_token_count': 568, 'stop_reason': 'eos_token'}]}{'model_id': 'ibm/granite-13b-instruct-v2', 'created_at': '2024-04-08T12:47:23.422Z', 'results': [{'generated_text': '[1]', 'generated_token_count': 4, 'input_token_count': 610, 'stop_reason': 'eos_token'}]}

{'model_id': 'ibm/granite-13b-instruct-v2', 'created_at': '2024-04-08T12:47:23.513Z', 'results': [{'generated_text': ' ${produce the answer}. The House of Habsburg is a European royal house with a long', 'generated_token_count': 20, 'input_token_count': 647, 'stop_reason': 'max_tokens'}]}
{'model_id': 'ibm/granite-13b-instruct-v2', 'created_at': '2024-04-08T12:47:23.629Z', 'results': [{'generated_text': 'Lindsey Buckingham/Dallas Taylor | Lindsey Buckingham/Dallas Taylor may refer to:', 'generated_token_count': 20, 'input_token_count': 402, 'stop_reason': 'max_token

Average Metric: 51 / 299  (17.1): 100%|█████████▉| 299/300 [02:50<00:00,  2.00it/s]

{'model_id': 'ibm/granite-13b-instruct-v2', 'created_at': '2024-04-08T12:47:24.016Z', 'results': [{'generated_text': 'continental history', 'generated_token_count': 4, 'input_token_count': 671, 'stop_reason': 'eos_token'}]}
{'model_id': 'ibm/granite-13b-instruct-v2', 'created_at': '2024-04-08T12:47:24.820Z', 'results': [{'generated_text': ' ${produce the answer}. Lindsey Buckingham and Dallas Taylor are both lead guitarists.\n\n', 'generated_token_count': 20, 'input_token_count': 528, 'stop_reason': 'max_tokens'}]}


Average Metric: 51 / 300  (17.0): 100%|██████████| 300/300 [02:52<00:00,  1.74it/s]

{'model_id': 'ibm/granite-13b-instruct-v2', 'created_at': '2024-04-08T12:47:26.158Z', 'results': [{'generated_text': 'yes', 'generated_token_count': 2, 'input_token_count': 550, 'stop_reason': 'eos_token'}]}
Average Metric: 51 / 300  (17.0%)
## Suggestions Score: 39.0
## Retrieval Score: 20.33
## Accuracy Score: 17.0


In [17]:
# No Compilation + Yes Assertion
baleen_with_assertions = assert_transform_module(SimplifiedBaleenAssertions().map_named_predictors(Retry), backtrack_handler) 
evaluate(baleen_with_assertions)

  0%|          | 0/300 [00:00<?, ?it/s]

{'model_id': 'ibm/granite-13b-instruct-v2', 'created_at': '2024-04-08T12:47:27.421Z', 'results': [{'generated_text': ' ${produce the query}. Cangzhou and Qionghai are cities in Hebei', 'generated_token_count': 20, 'input_token_count': 114, 'stop_reason': 'max_tokens'}]}
{'model_id': 'ibm/granite-13b-instruct-v2', 'created_at': '2024-04-08T12:47:27.995Z', 'results': [{'generated_text': 'Cangzhou Qionghai Hebei China', 'generated_token_count': 12, 'input_token_count': 138, 'stop_reason': 'eos_token'}]}
{'model_id': 'ibm/granite-13b-instruct-v2', 'created_at': '2024-04-08T12:47:28.843Z', 'results': [{'generated_text': ' ${produce the query}. Cangzhou is in the Hebei province of China. Q', 'generated_token_count': 20, 'input_token_count': 296, 'stop_reason': 'max_tokens'}]}
{'model_id': 'ibm/granite-13b-instruct-v2', 'created_at': '2024-04-08T12:47:30.172Z', 'results': [{'generated_text': 'Cangzhou ${is a} ${county} ${in} ${Hebei province}', 'generated_token_count': 20, 'input_token_count'

Average Metric: 0 / 1  (0.0):   0%|          | 1/300 [00:05<25:58,  5.21s/it]

{'model_id': 'ibm/granite-13b-instruct-v2', 'created_at': '2024-04-08T12:47:31.453Z', 'results': [{'generated_text': 'yes', 'generated_token_count': 2, 'input_token_count': 318, 'stop_reason': 'eos_token'}]}
{'cangzhou', 'qionghai'}
{'cangzhou', 'cang prefecture'}
{'model_id': 'ibm/granite-13b-instruct-v2', 'created_at': '2024-04-08T12:47:32.338Z', 'results': [{'generated_text': ' ${produce the query}. The National Hockey League conducts the draft for the 2017-18 season', 'generated_token_count': 20, 'input_token_count': 122, 'stop_reason': 'max_tokens'}]}
{'model_id': 'ibm/granite-13b-instruct-v2', 'created_at': '2024-04-08T12:47:33.438Z', 'results': [{'generated_text': 'Who conducts the draft in which Marc-Andre Fleury was drafted to the Vegas Golden Knights', 'generated_token_count': 20, 'input_token_count': 146, 'stop_reason': 'max_tokens'}]}
{'model_id': 'ibm/granite-13b-instruct-v2', 'created_at': '2024-04-08T12:47:34.180Z', 'results': [{'generated_text': 'Who conducts the draft 

Average Metric: 0 / 2  (0.0):   1%|          | 2/300 [00:13<35:46,  7.20s/it]

...

{'model_id': 'ibm/granite-13b-instruct-v2', 'created_at': '2024-04-08T12:47:55.119Z', 'results': [{'generated_text': 'River Tyne is a river in Midlothian, Scotland.', 'generated_token_count': 16, 'input_token_count': 437, 'stop_reason': 'eos_token'}]}
{'crichton collegiate church', 'crichton castle'}
{'crichton collegiate church', 'haltwhistle a69 bridge west', 'crichton castle', 'haltwhistle a69 bridge east'}
{'model_id': 'ibm/granite-13b-instruct-v2', 'created_at': '2024-04-08T12:47:55.940Z', 'results': [{'generated_text': ' ${produce the query}. Ealhswith was the daughter of Aethelberht', 'generated_token_count': 20, 'input_token_count': 123, 'stop_reason': 'max_tokens'}]}
{'model_id': 'ibm/granite-13b-instruct-v2', 'created_at': '2024-04-08T12:47:57.158Z', 'results': [{'generated_text': 'Aethelberht * child Æthelweard\n\n---\n', 'generated_token_count': 17, 'input_token_count': 147, 'stop_reason': 'eos_token'}]}
{'model_id': 'ibm/granite-13b-instruct-v2', 'created_at': '2024-04-08T

Average Metric: 1 / 5  (20.0):   2%|▏         | 5/300 [00:35<34:59,  7.12s/it]

{'model_id': 'ibm/granite-13b-instruct-v2', 'created_at': '2024-04-08T12:48:01.892Z', 'results': [{'generated_text': 'Alfred the Great', 'generated_token_count': 5, 'input_token_count': 346, 'stop_reason': 'eos_token'}]}
{'ealhswith', 'æthelweard son of alfred'}
{'æthelweard son of alfred', 'æthelweard king of hwicce', 'æthelweard historian'}
{'model_id': 'ibm/granite-13b-instruct-v2', 'created_at': '2024-04-08T12:48:02.754Z', 'results': [{'generated_text': ' ${produce the query}. The Port Authority of New York and New Jersey operates the Newark Liberty International', 'generated_token_count': 20, 'input_token_count': 113, 'stop_reason': 'max_tokens'}]}
{'model_id': 'ibm/granite-13b-instruct-v2', 'created_at': '2024-04-08T12:48:03.961Z', 'results': [{'generated_text': 'The Newark Airport Exchange is at the northern edge of an airport that is operated by whom?\n\n', 'generated_token_count': 20, 'input_token_count': 137, 'stop_reason': 'eos_token'}]}
{'model_id': 'ibm/granite-13b-instruc

Average Metric: 2 / 6  (33.3):   2%|▏         | 6/300 [00:46<40:52,  8.34s/it]

{'model_id': 'ibm/granite-13b-instruct-v2', 'created_at': '2024-04-08T12:48:12.626Z', 'results': [{'generated_text': 'Port Authority of New York and New Jersey', 'generated_token_count': 9, 'input_token_count': 423, 'stop_reason': 'eos_token'}]}
{'newark liberty international airport', 'newark airport interchange'}
{'newark liberty international airport', 'donald trump', 'newark airport interchange', 'president of united states disambiguation'}
{'model_id': 'ibm/granite-13b-instruct-v2', 'created_at': '2024-04-08T12:48:13.783Z', 'results': [{'generated_text': ' ${produce the query}. The action of a Peruvian footballer known for his goal scoring ability', 'generated_token_count': 20, 'input_token_count': 126, 'stop_reason': 'max_tokens'}]}
{'model_id': 'ibm/granite-13b-instruct-v2', 'created_at': '2024-04-08T12:48:15.268Z', 'results': [{'generated_text': 'When did an event take place resulting in a win during a domestic double due to the action of a', 'generated_token_count': 20, 'input

In [21]:
max_bootstrapped_demos = 2

In [22]:
# Yes Compilation + No Assertion
baleen = SimplifiedBaleen()
teleprompter = BootstrapFewShotWithRandomSearch(
    metric=validate_context_and_answer_and_hops,
    max_bootstrapped_demos=max_bootstrapped_demos,
    num_candidate_programs=6,
)

compiled_baleen = teleprompter.compile(student = SimplifiedBaleen(), teacher = SimplifiedBaleen(), trainset = trainset, valset = devset)
evaluate(compiled_baleen)

Going to sample between 1 and 2 traces per predictor.
Will attempt to train 6 candidate sets.


  0%|          | 0/300 [00:00<?, ?it/s]

{'model_id': 'meta-llama/llama-2-70b-chat', 'created_at': '2024-04-08T12:52:27.303Z', 'results': [{'generated_text': ' answer this question. First, we need to find the location of Cangzhou. We can', 'generated_token_count': 20, 'input_token_count': 120, 'stop_reason': 'max_tokens'}], 'system': {'warnings': [{'message': 'This model is a Non-IBM Product governed by a third-party license that may impose use restrictions and other obligations. By using this model you agree to its terms as identified in the following URL.', 'id': 'disclaimer_warning', 'more_info': 'https://dataplatform.cloud.ibm.com/docs/content/wsj/analyze-data/fm-models.html?context=wx'}]}}
{'model_id': 'meta-llama/llama-2-70b-chat', 'created_at': '2024-04-08T12:52:27.303Z', 'results': [{'generated_text': ' find the answer. First, we need to find out which draft Marc-Andre Fleury was', 'generated_token_count': 20, 'input_token_count': 136, 'stop_reason': 'max_tokens'}], 'system': {'warnings': [{'message': 'This model is a

Average Metric: 0 / 2  (0.0):   0%|          | 1/300 [00:09<48:53,  9.81s/it]

{'model_id': 'meta-llama/llama-2-70b-chat', 'created_at': '2024-04-08T12:52:35.495Z', 'results': [{'generated_text': ' NHL', 'generated_token_count': 3, 'input_token_count': 658, 'stop_reason': 'eos_token'}], 'system': {'warnings': [{'message': 'This model is a Non-IBM Product governed by a third-party license that may impose use restrictions and other obligations. By using this model you agree to its terms as identified in the following URL.', 'id': 'disclaimer_warning', 'more_info': 'https://dataplatform.cloud.ibm.com/docs/content/wsj/analyze-data/fm-models.html?context=wx'}]}}
{'model_id': 'meta-llama/llama-2-70b-chat', 'created_at': '2024-04-08T12:52:35.517Z', 'results': [{'generated_text': ' Yes', 'generated_token_count': 2, 'input_token_count': 428, 'stop_reason': 'eos_token'}], 'system': {'warnings': [{'message': 'This model is a Non-IBM Product governed by a third-party license that may impose use restrictions and other obligations. By using this model you agree to its terms as

...

{'model_id': 'meta-llama/llama-2-70b-chat', 'created_at': '2024-04-08T13:27:58.131Z', 'results': [{'generated_text': ' Hipnotis\n\n---\n\nContext:\n[1] «The Great Fire |', 'generated_token_count': 20, 'input_token_count': 2005, 'stop_reason': 'max_tokens'}], 'system': {'warnings': [{'message': 'This model is a Non-IBM Product governed by a third-party license that may impose use restrictions and other obligations. By using this model you agree to its terms as identified in the following URL.', 'id': 'disclaimer_warning', 'more_info': 'https://dataplatform.cloud.ibm.com/docs/content/wsj/analyze-data/fm-models.html?context=wx'}]}}
{'model_id': 'meta-llama/llama-2-70b-chat', 'created_at': '2024-04-08T13:27:58.595Z', 'results': [{'generated_text': ' When was the University of Maryland founded? --- Context: N/A\n\n---\n\nContext', 'generated_token_count': 20, 'input_token_count': 344, 'stop_reason': 'max_tokens'}], 'system': {'warnings': [{'message': 'This model is a Non-IBM Product governe

Average Metric: 9.0 / 173  (5.2):  58%|█████▊    | 173/300 [05:55<04:39,  2.20s/it]

{'model_id': 'meta-llama/llama-2-70b-chat', 'created_at': '2024-04-08T13:28:01.105Z', 'results': [{'generated_text': ' engineering\n\n---\n\nContext:\n[1] «The Great Victorian Collection | The', 'generated_token_count': 20, 'input_token_count': 932, 'stop_reason': 'max_tokens'}], 'system': {'warnings': [{'message': 'This model is a Non-IBM Product governed by a third-party license that may impose use restrictions and other obligations. By using this model you agree to its terms as identified in the following URL.', 'id': 'disclaimer_warning', 'more_info': 'https://dataplatform.cloud.ibm.com/docs/content/wsj/analyze-data/fm-models.html?context=wx'}]}}
{'model_id': 'meta-llama/llama-2-70b-chat', 'created_at': '2024-04-08T13:28:01.114Z', 'results': [{'generated_text': ' find the answer. We know that John Laub is a Distinguished University Professor in the Department', 'generated_token_count': 20, 'input_token_count': 1146, 'stop_reason': 'max_tokens'}], 'system': {'warnings': [{'message':

Average Metric: 9.0 / 174  (5.2):  58%|█████▊    | 174/300 [05:58<05:44,  2.73s/it]

{'model_id': 'meta-llama/llama-2-70b-chat', 'created_at': '2024-04-08T13:28:05.070Z', 'results': [{'generated_text': ' CGI-animated\n\n---\n\nContext:\n[1] «The Great Fire', 'generated_token_count': 20, 'input_token_count': 2055, 'stop_reason': 'max_tokens'}], 'system': {'warnings': [{'message': 'This model is a Non-IBM Product governed by a third-party license that may impose use restrictions and other obligations. By using this model you agree to its terms as identified in the following URL.', 'id': 'disclaimer_warning', 'more_info': 'https://dataplatform.cloud.ibm.com/docs/content/wsj/analyze-data/fm-models.html?context=wx'}]}}


In [ ]:
# Yes Compilation + Yes Assertion
baleen = SimplifiedBaleen()
teleprompter = BootstrapFewShotWithRandomSearch(
    metric=validate_context_and_answer_and_hops,
    max_bootstrapped_demos=max_bootstrapped_demos,
    num_candidate_programs=6,
)
compiled_baleen = teleprompter.compile(
    student=assert_transform_module(
        SimplifiedBaleenAssertions().map_named_predictors(Retry),
        backtrack_handler,
    ),
    teacher=baleen,
    trainset=trainset,
    valset=devset
)
evaluate(compiled_baleen)
